In [1]:
%load_ext dotenv

%dotenv ../tests/.env.test
%dotenv -o ../.env

In [2]:
from redbox.app import Redbox
from redbox.models.chain import RedboxQuery, RedboxState, ChainChatMessage

In [3]:
app = Redbox(debug=False)

INFO:elastic_transport.transport:HEAD http://localhost:9200/_alias/redbox-data-chunk-current [status:200 duration:0.008s]
INFO:elastic_transport.transport:HEAD http://localhost:9200/redbox-data-chat-mesage-log [status:200 duration:0.005s]


In [4]:
s = RedboxState(
    request=RedboxQuery(
        question="@gadget what is it about?",
        s3_keys=[],
        user_uuid="5210311c-df38-430f-8451-df5fa28f0be3",  # Get this from the URL in the admin console while viewing your local superuser
        chat_history=[
            ChainChatMessage(role="user", text="What is this report?"),
            ChainChatMessage(
                role="ai", text="The report is Tony_Blair_Institute__Governing_in_the_Age_of_AI__May_2024"
            ),
        ],
        permitted_s3_keys=["ai_tests/Tony_Blair_Institute__Governing_in_the_Age_of_AI__May_2024__2_.pdf"],
    )
)

In [5]:
## To use with Langfuse (see DEVELOPER_SETUP)

# Uncomment the below to use the langfuse auto-magic configuration to send traces to local langfuse


In [6]:
response_text = ""
citations = []
activity_log = []


async def token_handler(s):
    global response_text
    response_text += s


async def citations_handler(cs):
    citations.extend(cs)


async def activity_handler(e):
    activity_log.append(e)


r = await app.run(
    input=s,
    response_tokens_callback=token_handler,
    citations_callback=citations_handler,
    activity_event_callback=activity_handler,
)

print("*" * 10)
print()
print(f"User: {r.request.question}")
print()
print("Activity Log:")
for log in activity_log:
    print(f"\t - {log.message}")
print()
print(f"AI: {response_text}")
print()
print("Citations: ")
for c in citations:
    print(c.text_in_answer)
    for source in c.sources:
        print(f"[{source.source_type}] {source.source}")
        print("\t" + source.highlighted_text_in_source)

INFO:redbox.app:Request: {'question': '@gadget what is it about?', 's3_keys': [], 'chat_history': [{'role': 'user', 'text': 'What is this report?'}, {'role': 'ai', 'text': 'The report is Tony_Blair_Institute__Governing_in_the_Age_of_AI__May_2024'}], 'user_uuid': UUID('5210311c-df38-430f-8451-df5fa28f0be3'), 'permitted_s3_keys': ['ai_tests/Tony_Blair_Institute__Governing_in_the_Age_of_AI__May_2024__2_.pdf']}
INFO:elastic_transport.transport:POST http://localhost:9200/redbox-data-chunk-current/_search?scroll=5m [status:200 duration:0.003s]
INFO:elastic_transport.transport:DELETE http://localhost:9200/_search/scroll [status:200 duration:0.002s]


[-1:checkpoint] State at the end of step -1:
{'documents': DocumentState(groups={}), 'messages': []}
[0:tasks] Starting 1 task for step 0:
- __start__ -> RedboxState(request=RedboxQuery(question='@gadget what is it about?', s3_keys=[], user_uuid=UUID('5210311c-df38-430f-8451-df5fa28f0be3'), chat_history=[{'role': 'user', 'text': 'What is this report?'}, {'role': 'ai', 'text': 'The report is Tony_Blair_Institute__Governing_in_the_Age_of_AI__May_2024'}], ai_settings=AISettings(context_window_size=128000, llm_max_tokens=1024, max_document_tokens=1000000, self_route_enabled=False, map_max_concurrency=128, stuff_chunk_context_ratio=0.75, recursion_limit=50, system_info_prompt='You are Redbox, an AI assistant to civil servants in the United Kingdom.', persona_info_prompt='You follow instructions and respond to queries accurately and concisely, and are professional in all your interactions with users.', caller_info_prompt='', chat_system_prompt='You are tasked with providing information objec

INFO:elastic_transport.transport:POST http://localhost:9200/redbox-data-chunk-current/_search [status:200 duration:0.004s]


[5:writes] Finished step 5 with writes to 1 channel:
- messages -> [ToolMessage(content='null', name='_search_documents', tool_call_id='call_YYsPZqBwLeof84rmbkt3A7rh')]
[5:checkpoint] State at the end of step 5:
{'citations': [],
 'documents': DocumentState(groups={}),
 'messages': [AIMessage(content='', additional_kwargs={}, response_metadata={}, id='075e6d21-195c-456b-9c66-d6d0d754cc84', tool_calls=[{'name': '_search_documents', 'args': {'query': 'Tony_Blair_Institute__Governing_in_the_Age_of_AI__May_2024'}, 'id': 'call_YYsPZqBwLeof84rmbkt3A7rh', 'type': 'tool_call'}]),
              ToolMessage(content='null', name='_search_documents', id='744e723b-86ab-4069-8896-f6870cf26413', tool_call_id='call_YYsPZqBwLeof84rmbkt3A7rh')],
 'metadata': RequestMetadata(llm_calls=[LLMCallMetadata(id='8804a192-f03f-448d-b3ea-b9bc153a2b8f', llm_model_name='gpt-4o', input_tokens=787, output_tokens=0, timestamp=datetime.datetime(2024, 11, 19, 16, 57, 38, 221694, tzinfo=datetime.timezone.utc))], selected

INFO:elastic_transport.transport:POST http://localhost:9200/redbox-data-chunk-current/_search [status:200 duration:0.009s]


[7:writes] Finished step 7 with writes to 3 channels:
- metadata -> RequestMetadata(llm_calls=[LLMCallMetadata(id='4981e188-1722-4b9b-8193-61429a53c7c3', llm_model_name='gpt-4o', input_tokens=794, output_tokens=0, timestamp=datetime.datetime(2024, 11, 19, 16, 57, 39, 327262, tzinfo=datetime.timezone.utc))], selected_files_total_tokens=0, number_of_selected_files=0)
- citations -> []
- messages -> [AIMessage(content='', additional_kwargs={}, response_metadata={}, tool_calls=[{'name': '_search_documents', 'args': {'query': 'Governing in the Age of AI Tony Blair Institute May 2024'}, 'id': 'call_MyD0DH7OETuL79Pxww10uZKR', 'type': 'tool_call'}])]
[7:checkpoint] State at the end of step 7:
{'citations': [],
 'documents': DocumentState(groups={}),
 'messages': [AIMessage(content='', additional_kwargs={}, response_metadata={}, id='075e6d21-195c-456b-9c66-d6d0d754cc84', tool_calls=[{'name': '_search_documents', 'args': {'query': 'Tony_Blair_Institute__Governing_in_the_Age_of_AI__May_2024'}, 'i

INFO:elastic_transport.transport:POST http://localhost:9200/redbox-data-chunk-current/_search [status:200 duration:0.002s]


[11:writes] Finished step 11 with writes to 3 channels:
- metadata -> RequestMetadata(llm_calls=[LLMCallMetadata(id='e14096de-7cd6-4ed5-a91f-b0268663bfb4', llm_model_name='gpt-4o', input_tokens=801, output_tokens=0, timestamp=datetime.datetime(2024, 11, 19, 16, 57, 41, 78002, tzinfo=datetime.timezone.utc))], selected_files_total_tokens=0, number_of_selected_files=0)
- citations -> []
- messages -> [AIMessage(content='', additional_kwargs={}, response_metadata={}, tool_calls=[{'name': '_search_documents', 'args': {'query': 'Tony Blair Institute Governing in the Age of AI May 2024'}, 'id': 'call_bQe90xOHJDPhAE8FwUpfpN4n', 'type': 'tool_call'}, {'name': '_search_wikipedia', 'args': {'query': 'Tony Blair Institute Governing in the Age of AI May 2024'}, 'id': 'call_K0aMUpAjE1lvMNisBUNyZ3W6', 'type': 'tool_call'}, {'name': '_search_govuk', 'args': {'query': 'Tony Blair Institute Governing in the Age of AI May 2024'}, 'id': 'call_lyRlbn5PfqJCcfjmsDUFMlkQ', 'type': 'tool_call'}])]
[11:checkpoi

In [7]:
str(r.messages[-1])

'content="The report titled \'Tony Blair Institute: Governing in the Age of AI\' is presumably an analysis or guidance document produced by the Tony Blair Institute in May 2024, focusing on the implications and strategies for governance in the context of advancing artificial intelligence." additional_kwargs={} response_metadata={} id=\'ff3247ae-5a5f-42d7-9cde-f7d062153a19\''